##### Steps to detect duration and frequency of ball bouncing from wav file
1. Import necessary libraries
2. Open audio File
3. Detect periods of activity
4. For Each period, find the frequency of the ball
5. Output: 
    1. Plot a graph identifying periods of activity 
    2. Plot a sample period sinsoidal wave over activity
    3. Output excel file with columns: start period, end period, duration, frequency, number of bounces

1. Import necessary libraries

In [22]:
from pydub import AudioSegment
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from pydub.utils import mediainfo
import numpy, scipy.optimize
import pandas as pd

2. Open audio File

In [ ]:
FILE_NAME='./sound_of_ball_original.wav'
info = mediainfo(FILE_NAME)
original_sample_rate=int(info['sample_rate'])
sound = AudioSegment.from_file(FILE_NAME)
# saved for easy opening using Sonic Visualizer app: https://www.sonicvisualiser.org/
file_handle = sound.export("sound_of_ball_original_2.wav", format="wav")
samples = sound.get_array_of_samples()
samples_list=samples.tolist()

3. Detect periods of activity

In [ ]:
# 80 th percentile and window size of 100 are good estimates
window_size=1000
abs_samples_list = [abs(ele) for ele in samples_list]
abs_samples_list_pd=pd.Series(abs_samples_list)
req_percentile=np.percentile(abs_samples_list,80)
max_val=max(abs_samples_list)
# [f(x) if condition else g(x) for x in sequence]
signal_on=[max_val if x >req_percentile else 0 for x in abs_samples_list]
block_signal_on=signal_on.copy()
for i in range(window_size, len(samples_list)-window_size):
    if max_val in signal_on[i-window_size:i+window_size]:
        block_signal_on[i]=max_val
plt.figure(figsize=(10,6),dpi=600)
plt.plot(samples_list)
plt.plot(block_signal_on,'g')
plt.show()

Identify periods of activity start and end

In [ ]:
signal_on_periods=[]
period_start=-1
period_end=-1
for i in range(len(block_signal_on)):
    if block_signal_on[i]!=0:
        if period_start==-1:
            period_start=i
    else:
        if period_start!=-1 and period_end==-1:
            period_end = i
            signal_on_periods.append(tuple([period_start, period_end]))
            period_start=period_end=-1

Curve Fitting to Sine wave

In [ ]:
def sinfunc(t, A, w, p, c):
    return A * numpy.sin(w*t + p) + c
def fit_sin(tt, yy):
    '''Fit sin to the input time sequence, and return fitting parameters "amp", "omega", "phase", "offset", "freq", "period" and "fitfunc"'''
    tt = numpy.array(tt)
    yy = numpy.array(yy)
    ff = numpy.fft.fftfreq(len(tt), (tt[1]-tt[0]))   # assume uniform spacing
    Fyy = abs(numpy.fft.fft(yy))
    guess_freq = abs(ff[numpy.argmax(Fyy[1:])+1])   # excluding the zero frequency "peak", which is related to offset
    guess_amp = numpy.std(yy) * 2.**0.5
    guess_offset = numpy.mean(yy)
    guess = numpy.array([guess_amp, 2.*numpy.pi*guess_freq, 0., guess_offset])

    popt, pcov = scipy.optimize.curve_fit(sinfunc, tt, yy, p0=guess)
    A, w, p, c = popt
    f = w/(2.*numpy.pi)
    fitfunc = lambda t: A * numpy.sin(w*t + p) + c
    return {"amp": A, "omega": w, "phase": p, "offset": c, "freq": f, "period": 1./f, "fitfunc": fitfunc, "maxcov": numpy.max(pcov), "rawres": (guess,popt,pcov)}

4. For Each period, find the frequency of the ball

Note: I verified the correctness by slowing down the audio file and counting the bounces. For Example:



In [27]:
all_result_dict={}
period_index=0
for period_start, period_end in signal_on_periods:
    one_result_dict={}
    one_result_dict['start']=period_start
    one_result_dict['end']=period_end
    one_sample=samples[period_start:period_end]
    x_vals=np.linspace(0,len(one_sample)-1, num=len(one_sample))
    x_vals_test=np.linspace(0,len(one_sample)-1, num=10* len(one_sample))

    res = fit_sin(x_vals, one_sample)
    # print( "Amplitude=%(amp)s, Angular freq.=%(omega)s, phase=%(phase)s, offset=%(offset)s, Max. Cov.=%(maxcov)s" % res )
    # plt.figure(figsize=(160, 8))
    # plt.plot(x_vals[:len(one_sample)], one_sample, label='Data')
    # plt.plot(x_vals_test, res["fitfunc"](x_vals_test), "r-", label="y fit curve", linewidth=2)
    # plt.legend(loc='best')
    # plt.show()
    one_result_dict['period_index']=period_index
    one_result_dict['the_freq']=res['omega']/(2*np.pi)
    one_result_dict['bounce_count']=int(one_result_dict['the_freq']*(period_end-period_start))
    one_result_dict['period_duration']=(period_end-period_start)/original_sample_rate
    print('The bouncing frequency:', one_result_dict['the_freq'], end='\t')
    print('Period bounce count:',one_result_dict['bounce_count'], end='\t')
    print('Period duration:', one_result_dict['period_duration'])
    all_result_dict[period_index]=one_result_dict.copy()
    period_index+=1


The bouncing frequency: 0.0017502743083820183	Period bounce count: 3	Period duration: 0.046099773242630385
The bouncing frequency: 0.0006750183117548302	Period bounce count: 30	Period duration: 1.0378684807256235
The bouncing frequency: 0.0012892234973527195	Period bounce count: 54	Period duration: 0.9659863945578231
The bouncing frequency: 0.0012707600624516306	Period bounce count: 63	Period duration: 1.1255328798185942
The bouncing frequency: 0.0011959766972566262	Period bounce count: 57	Period duration: 1.0889569160997732
The bouncing frequency: 0.0011789842619774153	Period bounce count: 52	Period duration: 1.001111111111111
The bouncing frequency: 0.0012128345367179712	Period bounce count: 45	Period duration: 0.8443537414965986
The bouncing frequency: 0.0012204533450750179	Period bounce count: 53	Period duration: 0.9932426303854875
The bouncing frequency: 0.0012570585737505682	Period bounce count: 53	Period duration: 0.9588208616780045
The bouncing frequency: 0.001258215961524728	P

Export to Excel file

In [28]:
all_result_dict

{0: {'start': 20305,
  'end': 22338,
  'period_index': 0,
  'the_freq': 0.0017502743083820183,
  'bounce_count': 3,
  'period_duration': 0.046099773242630385},
 1: {'start': 117296,
  'end': 163066,
  'period_index': 1,
  'the_freq': 0.0006750183117548302,
  'bounce_count': 30,
  'period_duration': 1.0378684807256235},
 2: {'start': 224408,
  'end': 267008,
  'period_index': 2,
  'the_freq': 0.0012892234973527195,
  'bounce_count': 54,
  'period_duration': 0.9659863945578231},
 3: {'start': 353830,
  'end': 403466,
  'period_index': 3,
  'the_freq': 0.0012707600624516306,
  'bounce_count': 63,
  'period_duration': 1.1255328798185942},
 4: {'start': 479804,
  'end': 527827,
  'period_index': 4,
  'the_freq': 0.0011959766972566262,
  'bounce_count': 57,
  'period_duration': 1.0889569160997732},
 5: {'start': 599879,
  'end': 644028,
  'period_index': 5,
  'the_freq': 0.0011789842619774153,
  'bounce_count': 52,
  'period_duration': 1.001111111111111},
 6: {'start': 760403,
  'end': 79763

In [29]:
all_df=pd.DataFrame()
all_df.size

0

In [35]:
all_df=pd.DataFrame()
for period_index, period_details in all_result_dict.items():
    if all_df.size==0:
        all_df = pd.DataFrame(data=period_details, index=[0])
    else:
        one_df=pd.DataFrame(data=period_details, index=[0])
        all_df=pd.concat([all_df,one_df])

all_df.to_excel('./'+FILE_NAME+'Ball_Bounces.xlsx')


#### Appendix and helper functions

In [ ]:
def speed_change(sound, speed=1.0):
    # Manually override the frame_rate. This tells the computer how many
    # samples to play per second
    sound_with_altered_frame_rate = sound._spawn(sound.raw_data, overrides={
        "frame_rate": int(sound.frame_rate * speed)
    })

    # convert the sound with altered frame rate to a standard frame rate
    # so that regular playback programs will work right. They often only
    # know how to play audio at standard frame rate (like 44.1k)
    return sound_with_altered_frame_rate.set_frame_rate(sound.frame_rate)

One Sample audio file

In [ ]:
one_sample=samples[100000:180000]
short_sound = AudioSegment(one_sample.tobytes(), frame_rate=sound.frame_rate,sample_width=sound.sample_width,channels=1)
file_handle = short_sound.export("short_sound_output.wav", format="wav")
plt.figure(figsize=[20,8])
plt.plot(one_sample)